In [1]:
import sys 
sys.path.append('../')
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from NN import network, activation_functions, loss_functions
from NN import ANN


## Simple Run Checks
To identify if there is no code broken

In [2]:
from importlib import reload
reload(network)
I = np.array([[0.05, 0.10]])
W = np.array([[0.15, 0.2], [0.25, 0.3]]).T
h1 = network.Layer(2, 2, 'sigmoid', weights=W, bias=0.35, label="H1")
netH, outH =  h1.feed_forward(I)
print(netH)
print(outH)

[[0.3775 0.3925]]
[[0.59326999 0.59688438]]


In [3]:
from importlib import reload
reload(network)
I = np.array([[0.59326999, 0.59688438]])
W = np.array([[0.4, 0.45], [0.50, 0.55]]).T
o1 = network.Layer(2, 2, 'sigmoid', weights=W, bias=0.6, label="H1")
netO, outO =  o1.feed_forward(I)
print(netO)
print(outO)

[[1.10590597 1.2249214 ]]
[[0.75136507 0.77292847]]


# Convergence Checkings
Based on the sample given by the class teacher

## Manual Calculations

In [4]:
from importlib import reload
reload(network)
model = network.NN(loss='smd')
X = np.array([[0.05, 0.10]])

Wh = np.array([[0.15, 0.2], [0.25, 0.3]]).T
h = network.Layer(2, 2, 'sigmoid', weights=Wh, bias=0.35, label="H1")

Wo = np.array([[0.4, 0.45], [0.50, 0.55]]).T
o = network.Layer(2, 2, 'sigmoid', weights=Wo, bias=0.6, label="H1")
model.add_layer(h)
model.add_layer(o)
model.show_weights()

Y, aY = model.feed_forward(X)
Y_, aY_ = ([1.10590597, 1.2249214 ], [0.75136507, 0.77292847])
print("Y\n",Y_)
print("\na(Y)\n",aY_)

assert((Y - Y_).sum() < np.finfo(np.float32).eps)
assert((aY - aY_).sum() < np.finfo(np.float32).eps)


Y
 [1.10590597, 1.2249214]

a(Y)
 [0.75136507, 0.77292847]


### Working on the back propagation

In [5]:
from importlib import reload
reload(network)
model.show_weights()
Y = np.array([0.01, 0.99])
Etotal = loss_functions.smd(aY, Y)
print(Etotal)
assert((Etotal - 0.2983711) < np.finfo(np.float32).eps)

0.2983711087600027


### Emulating the weights update for the layer O 

In [6]:
reload(loss_functions)
reload(activation_functions)
lr = 0.5
#Done - Partial
dEo_dw = loss_functions.smd_derivative_chain(outO, Y)
print(dEo_dw)

# Done
dOuto_Dneto = activation_functions.sigmoid_derivative_chain(outO)
print('dout',dOuto_Dneto)

# Done - Self.input
dNeto  = outH
print('dnet',dNeto) 
# Done
deltaO  = dEo_dw * dOuto_Dneto
print('delta', deltaO)

dWO = deltaO * outH
print('dw', dWO)
# Done
updateO = Wo - lr * dWO
print('update', updateO)

[[ 0.74136507 -0.21707153]]
dout [[0.1868156  0.17551005]]
dnet [[0.59326999 0.59688438]]
delta [[ 0.13849856 -0.03809824]]
dw [[ 0.08216704 -0.02274024]]
update [[0.35891648 0.51137012]
 [0.40891648 0.56137012]]


In [7]:
#
# Done - Partial
dEo_dOh = deltaO * Wo
dETotal_dOh = dEo_dOh.sum(axis=1)
print (dEo_dOh)
print('dETotal_dOh', dETotal_dOh)

# Done
dOuth_Dneth = activation_functions.sigmoid_derivative_chain(outH)
print('dOuth_Dneth', dOuth_Dneth)


# Done
deltaH = dETotal_dOh * dOuth_Dneth 
print('deltaH', deltaH)

# done
# self.input
dNeth_dw = X
dWh = deltaH * dNeth_dw
print('dWh', dWh)

# Done
updateH = Wh - lr * dWh
print('update', updateH)

[[ 0.05539942 -0.01904912]
 [ 0.06232435 -0.02095403]]
dETotal_dOh [0.03635031 0.04137032]
dOuth_Dneth [[0.24130071 0.24061342]]
deltaH [[0.00877135 0.00995425]]
dWh [[0.00043857 0.00099543]]
update [[0.14978072 0.24950229]
 [0.19978072 0.29950229]]


## Using the implemented Grad calculation for Layers

In [8]:
reload(loss_functions)
reload(activation_functions)
reload(network)
network.DEBUG = False

X = np.array([[0.05, 0.10]], np.float64)

Wh = np.array([[0.15, 0.2], [0.25, 0.3]], np.float64).T
h = network.Layer(2, 2, 'sigmoid', weights=Wh, bias=0.35, label="H1")

Wo = np.array([[0.4, 0.45], [0.50, 0.55]], np.float64).T
o = network.Layer(2, 2, 'sigmoid', weights=Wo, bias=0.6, label="H1")
Y = np.array([0.01, 0.99], np.float64)

for i in range(10000):
    netH, outH = h.feed_forward(X)
    netO, outO = o.feed_forward(outH)

    
    Etotal = loss_functions.smd(outO, Y)
    if (i % 1000) == 0:
        print(i, 'error', Etotal)
    
    dEo_dw = loss_functions.smd_derivative_chain(outO, Y)
    network.dprint(dEo_dw)
    network.dprint ("")
    network.dprint ("==========================================")
    network.dprint ("Back Propagate Layer O")
    network.dprint ("==========================================")
    o.backpropagate(dETotal_dOut=dEo_dw)
    network.dprint ("==========================================")
    network.dprint ("")

    network.dprint ("==========================================")
    network.dprint ("Back Propagate Layer H")
    network.dprint ("==========================================")
    h.backpropagate(output_layer=o)
    network.dprint ("==========================================")

print (outO)

0 error 0.2983711087600027
1000 error 0.001114349453733746
2000 error 0.00044486770391326887
3000 error 0.00025152360241099405
4000 error 0.00016427727363225536
5000 error 0.00011622569943793622
6000 error 8.653979465934606e-05
7000 error 6.676957838285888e-05
8000 error 5.288555201099971e-05
9000 error 4.2742284255545085e-05
[[0.01591419 0.98406371]]


# Using the Fit Methods with the full network calculation

## SMD as the Loss Function

In [9]:
from utils import dataset_helper
reload(loss_functions)
reload(activation_functions)
reload(network)
reload(dataset_helper)
network.DEBUG = False
eps = 0.00001

X = np.array([[0.05, 0.10]], np.float64)
Y = np.array([[0.01, 0.99]], np.float64)

Wh = np.array([[0.15, 0.2], [0.25, 0.3]], np.float64).T
h = network.Layer(2, 2, 'sigmoid', weights=Wh, bias=0.35, label="H1")

Wo = np.array([[0.4, 0.45], [0.50, 0.55]], np.float64).T
o = network.Layer(2, 2, 'sigmoid', weights=Wo, bias=0.6, label="Output")

model = network.NN(loss='smd')
model.add_layer(h)
model.add_layer(o)
model.show_weights()

model.fit(X, Y, max_iter=50000, 
          lr=0.5, epsilon=eps, 
          print_interval=2000)

_, Y_ = model.feed_forward(X)

mae = np.absolute(Y - Y_).mean()
print(Y_, mae)
assert(mae < 0.01)

It: 1 Batch: 1 Epoch 0 Error: 0.29837111 lr: 0.50000000 
It: 2000 Batch: 1 Epoch 1999 Error: 0.00087915 lr: 0.50000000 
It: 4000 Batch: 1 Epoch 3999 Error: 0.00034362 lr: 0.50000000 
It: 6000 Batch: 1 Epoch 5999 Error: 0.00019080 lr: 0.50000000 
It: 8000 Batch: 1 Epoch 7999 Error: 0.00012257 lr: 0.50000000 
It: 10000 Batch: 1 Epoch 9999 Error: 0.00008538 lr: 0.50000000 
It: 12000 Batch: 1 Epoch 11999 Error: 0.00006263 lr: 0.50000000 
It: 14000 Batch: 1 Epoch 13999 Error: 0.00004763 lr: 0.50000000 
It: 16000 Batch: 1 Epoch 15999 Error: 0.00003719 lr: 0.50000000 
It: 18000 Batch: 1 Epoch 17999 Error: 0.00002965 lr: 0.50000000 
It: 20000 Batch: 1 Epoch 19999 Error: 0.00002402 lr: 0.50000000 
It: 22000 Batch: 1 Epoch 21999 Error: 0.00001971 lr: 0.50000000 
It: 24000 Batch: 1 Epoch 23999 Error: 0.00001636 lr: 0.50000000 
It: 26000 Batch: 1 Epoch 25999 Error: 0.00001370 lr: 0.50000000 
It: 28000 Batch: 1 Epoch 27999 Error: 0.00001156 lr: 0.50000000 
Finished 
 It: 29778 Batch: 1 Epoch 29777 

## Cross Entropy 

In [10]:
from utils import dataset_helper
reload(loss_functions)
reload(activation_functions)
reload(network)
reload(dataset_helper)
network.DEBUG = False
eps = 0.117
X = np.array([[0.05, 0.10]], np.float64)
Y = np.array([[0.01, 0.99]], np.float64)

Wh = np.array([[0.15, 0.2], [0.25, 0.3]], np.float64).T
h = network.Layer(2, 2, 'sigmoid', weights=Wh, bias=0.35, label="H1")

Wo = np.array([[0.4, 0.45], [0.50, 0.55]], np.float64).T
o = network.Layer(2, 2, 'sigmoid', weights=Wo, bias=0.6, label="Output")

model = network.NN(loss='cross_entropy')
model.add_layer(h)
model.add_layer(o)
model.show_weights()

model.fit(X, Y, max_iter=50000, 
          lr=0.1, epsilon=eps, 
          print_interval=2000)

_, Y_ = model.feed_forward(X)

mae = np.absolute(Y - Y_).mean()
print(Y_, mae)
assert(mae < 0.01)

It: 1 Batch: 1 Epoch 0 Error: 1.65052853 lr: 0.10000000 
It: 2000 Batch: 1 Epoch 1999 Error: 0.23026661 lr: 0.10000000 
It: 4000 Batch: 1 Epoch 3999 Error: 0.17763656 lr: 0.10000000 
It: 6000 Batch: 1 Epoch 5999 Error: 0.15757797 lr: 0.10000000 
It: 8000 Batch: 1 Epoch 7999 Error: 0.14673802 lr: 0.10000000 
It: 10000 Batch: 1 Epoch 9999 Error: 0.13988631 lr: 0.10000000 
It: 12000 Batch: 1 Epoch 11999 Error: 0.13514499 lr: 0.10000000 
It: 14000 Batch: 1 Epoch 13999 Error: 0.13166350 lr: 0.10000000 
It: 16000 Batch: 1 Epoch 15999 Error: 0.12899745 lr: 0.10000000 
It: 18000 Batch: 1 Epoch 17999 Error: 0.12689090 lr: 0.10000000 
It: 20000 Batch: 1 Epoch 19999 Error: 0.12518550 lr: 0.10000000 
It: 22000 Batch: 1 Epoch 21999 Error: 0.12377782 lr: 0.10000000 
It: 24000 Batch: 1 Epoch 23999 Error: 0.12259734 lr: 0.10000000 
It: 26000 Batch: 1 Epoch 25999 Error: 0.12159422 lr: 0.10000000 
It: 28000 Batch: 1 Epoch 27999 Error: 0.12073225 lr: 0.10000000 
It: 30000 Batch: 1 Epoch 29999 Error: 0.11

In [11]:
from utils import dataset_helper
reload(loss_functions)
reload(activation_functions)
reload(network)
reload(dataset_helper)
network.DEBUG = False

eps = np.finfo(np.float32).eps

X = np.array([[0.05, 0.10]], np.float64)
Y = np.array([[0.01, 0.99]], np.float64)

h1 = network.Layer(2, 3, 'sigmoid',  bias=0.35, label="H1")
o = network.Layer(3, 2, 'sigmoid', bias=0.6, label="Output")

model = network.NN(loss='smd')
model.add_layer(h1)
model.add_layer(o)
model.show_weights()

model.fit(X, Y, max_iter=50000, 
          lr=0.1, epsilon=eps, 
          print_interval=2000)

_, Y_ = model.feed_forward(X)

mae = np.absolute(Y - Y_).mean()
print(Y_, mae)
assert(mae < 0.01)

Model Weights
-------------------------------
H1      (input=2, neurons=3, activation=sigmoid)
[[0.44929645 0.79646784 0.79103829]
 [0.72992999 0.57560544 0.96155656]]
Output  (input=3, neurons=2, activation=sigmoid)
[[0.29784028 0.66417762]
 [0.97638038 0.32397302]
 [0.77332224 0.73769547]]
-------------------------------
('H1', (1, 2), (2, 3))
('net', array([[0.44545782, 0.44738394, 0.48570757]]))
('out', array([[0.60955875, 0.61001706, 0.61909473]]))
('Output', (1, 3), (3, 2))
('net', array([[1.85591956, 1.65918772]]))
('out', array([[0.86482063, 0.84012893]]))
('dETotal_dOut', array([[ 0.52106339, -0.09135522],
       [ 0.52145517, -0.09142391],
       [ 0.52921494, -0.09278439]]))
('self.dOut_dNet', array([[0.11690591, 0.13431231]]))
('self.delta', array([[ 0.06091539, -0.01227013],
       [ 0.06096119, -0.01227936],
       [ 0.06186835, -0.01246209]]))
('self.dW', (3, 2), (1, 3))
('self.dW', array([[ 0.03713151, -0.00747937],
       [ 0.03718737, -0.00749062],
       [ 0.03830237

       [ 0.03956529, -0.00758107]]))
('calc_dETotal_dOut', array([[ 0.01685017, -0.00808189],
       [ 0.05958901, -0.00398111],
       [ 0.04744356, -0.00910996]]))
('self.weights', array([[0.26386898, 0.67085111],
       [0.94236527, 0.33065513],
       [0.73828426, 0.74457852]]))
H1
('get_dETotal_dOut', array([0.00876828, 0.0556079 , 0.0383336 ]))
('dETotal_dOut', array([0.00876828, 0.0556079 , 0.0383336 ]))
('self.dOut_dNet', array([[0.23800276, 0.23793083, 0.23584195]]))
('self.delta', array([[0.00208688, 0.01323083, 0.00904067]]))
('self.dW', (1, 3), (1, 2))
('self.dW', array([[0.00010434, 0.00066154, 0.00045203],
       [0.00020869, 0.00132308, 0.00090407]]))
('calc_dETotal_dOut', array([[0.00093669, 0.01050294, 0.00713509],
       [0.00152139, 0.00754576, 0.00866026]]))
('self.weights', array([[0.44879345, 0.79349237, 0.78899527],
       [0.72892399, 0.5696545 , 0.95747052]]))
('H1', (1, 2), (2, 3))
('net', array([[0.44533207, 0.44664007, 0.48519682]]))
('out', array([[0.609528

('out', array([[0.81611169, 0.84836081]]))
('dETotal_dOut', array([[ 0.49129598, -0.08632397],
       [ 0.49098745, -0.08626976],
       [ 0.49856203, -0.08760067]]))
('self.dOut_dNet', array([[0.1500734 , 0.12864475]]))
('self.delta', array([[ 0.07373046, -0.01110513],
       [ 0.07368416, -0.01109815],
       [ 0.0748209 , -0.01126937]]))
('self.dW', (3, 2), (1, 3))
('self.dW', array([[ 0.04493605, -0.00676817],
       [ 0.04487963, -0.00675968],
       [ 0.04627505, -0.00696985]]))
('calc_dETotal_dOut', array([[ 0.0074895 , -0.0077553 ],
       [ 0.05748032, -0.00397487],
       [ 0.04272568, -0.00871033]]))
('self.weights', array([[0.09708589, 0.69903033],
       [0.77560265, 0.35883221],
       [0.56641195, 0.77361843]]))
H1
('get_dETotal_dOut', array([-0.0002658 ,  0.05350545,  0.03401535]))
('dETotal_dOut', array([-0.0002658 ,  0.05350545,  0.03401535]))
('self.dOut_dNet', array([[0.23801765, 0.2381013 , 0.23596306]]))
('self.delta', array([[-6.32653266e-05,  1.27397162e-02,  8.

('net', array([[0.44506846, 0.44297662, 0.48279453]]))
('out', array([[0.60946608, 0.60896807, 0.61840754]]))
('Output', (1, 3), (3, 2))
('net', array([[1.43963449, 1.72920204]]))
('out', array([[0.80839804, 0.84931032]]))
('dETotal_dOut', array([[ 0.48659652, -0.08574559],
       [ 0.48619892, -0.08567552],
       [ 0.49373537, -0.08700356]]))
('self.dOut_dNet', array([[0.15489065, 0.1279823 ]]))
('self.delta', array([[ 0.07536925, -0.01097392],
       [ 0.07530766, -0.01096495],
       [ 0.07647499, -0.01113492]]))
('self.dW', (3, 2), (1, 3))
('self.dW', array([[ 0.045935  , -0.00668823],
       [ 0.04585996, -0.0066773 ],
       [ 0.04729271, -0.00688592]]))
('calc_dETotal_dOut', array([[ 0.00560504, -0.00770802],
       [ 0.05670044, -0.00397141],
       [ 0.04152741, -0.00865275]]))
('self.weights', array([[0.06977417, 0.70306316],
       [0.74833125, 0.36285909],
       [0.53829023, 0.77777087]]))
H1
('get_dETotal_dOut', array([-0.00210298,  0.05272903,  0.03287467]))
('dETotal_d

       [-0.00023813,  0.00115629,  0.00064539]]))
('calc_dETotal_dOut', array([[-0.001068  ,  0.0089285 ,  0.00500459],
       [-0.00173436,  0.00609373,  0.00600442]]))
('self.weights', array([[0.44854773, 0.77188018, 0.7752766 ],
       [0.72843256, 0.52643011, 0.93003317]]))
('H1', (1, 2), (2, 3))
('net', array([[0.44527064, 0.44123702, 0.48176715]]))
('out', array([[0.6095142 , 0.60855375, 0.61816507]]))
('Output', (1, 3), (3, 2))
('net', array([[1.23588393, 1.75679816]]))
('out', array([[0.77484674, 0.8528082 ]]))
('dETotal_dOut', array([[ 0.46618495, -0.08362035],
       [ 0.46545035, -0.08348858],
       [ 0.47280154, -0.08480718]]))
('self.dOut_dNet', array([[0.17445927, 0.12552637]]))
('self.delta', array([[ 0.08133029, -0.01049656],
       [ 0.08120213, -0.01048002],
       [ 0.08248461, -0.01064554]]))
('self.dW', (3, 2), (1, 3))
('self.dW', array([[ 0.04957196, -0.0063978 ],
       [ 0.04941586, -0.00637766],
       [ 0.05098911, -0.0065807 ]]))
('calc_dETotal_dOut', array(

...

       [-0.00432128, -0.00245893]]))
('self.weights', array([[-2.06519773,  1.22416247],
       [-1.35184731,  0.87267035],
       [-1.64029695,  1.30788446]]))
H1
('get_dETotal_dOut', array([-0.00769629, -0.00508872, -0.00678021]))
('dETotal_dOut', array([-0.00769629, -0.00508872, -0.00678021]))
('self.dOut_dNet', array([[0.23454037, 0.23691307, 0.23359858]]))
('self.delta', array([[-0.00180509, -0.00120558, -0.00158385]]))
('self.dW', (1, 3), (1, 2))
('self.dW', array([[-9.02545587e-05, -6.02792167e-05, -7.91923215e-05],
       [-1.80509117e-04, -1.20558433e-04, -1.58384643e-04]]))
('calc_dETotal_dOut', array([[-0.00126257, -0.0010492 , -0.00149508],
       [-0.0022207 , -0.00087192, -0.00200736]]))
('self.weights', array([[0.69949726, 0.87031292, 0.94399753],
       [1.23033161, 0.7232956 , 1.26747504]]))
('H1', (1, 2), (2, 3))
('net', array([[0.50800802, 0.46584521, 0.52394738]]))
('out', array([[0.62433939, 0.6143999 , 0.62807033]]))
('Output', (1, 3), (3, 2))
('net', array([[-2.5

('Output', (1, 3), (3, 2))
('net', array([[-2.56293802,  2.73101738]]))
('out', array([[0.07156209, 0.93883229]]))
('dETotal_dOut', array([[ 0.03844225, -0.03195151],
       [ 0.03782821, -0.03144115],
       [ 0.0386711 , -0.03214173]]))
('self.dOut_dNet', array([[0.06644096, 0.05742622]]))
('self.delta', array([[ 0.00255414, -0.00183485],
       [ 0.00251334, -0.00180555],
       [ 0.00256935, -0.00184578]]))
('self.dW', (3, 2), (1, 3))
('self.dW', array([[ 0.00159492, -0.00114577],
       [ 0.00154438, -0.00110946],
       [ 0.00161397, -0.00115945]]))
('calc_dETotal_dOut', array([[-0.00529172, -0.00225486],
       [-0.00341377, -0.00158394],
       [-0.0042317 , -0.00242292]]))
('self.weights', array([[-2.07197827,  1.22901784],
       [-1.35841332,  0.87737209],
       [-1.64715862,  1.31279792]]))
H1
('get_dETotal_dOut', array([-0.00754657, -0.00499771, -0.00665462]))
('dETotal_dOut', array([-0.00754657, -0.00499771, -0.00665462]))
('self.dOut_dNet', array([[0.23451299, 0.2368960

('self.dOut_dNet', array([[0.23448676, 0.23687974, 0.23355028]]))
('self.delta', array([[-0.00173661, -0.00116356, -0.0015266 ]]))
('self.dW', (1, 3), (1, 2))
('self.dW', array([[-8.68305212e-05, -5.81780247e-05, -7.63302376e-05],
       [-1.73661042e-04, -1.16356049e-04, -1.52660475e-04]]))
('calc_dETotal_dOut', array([[-0.00122106, -0.00101549, -0.00144598],
       [-0.00214921, -0.00084725, -0.00194467]]))
('self.weights', array([[0.70316999, 0.87276985, 0.94722317],
       [1.23767708, 0.72820946, 1.27392631]]))
('H1', (1, 2), (2, 3))
('net', array([[0.50892621, 0.46645944, 0.52475379]]))
('out', array([[0.62455472, 0.61454541, 0.62825869]]))
('Output', (1, 3), (3, 2))
('net', array([[-2.57569731,  2.74018808]]))
('out', array([[0.07071897, 0.93935681]]))
('dETotal_dOut', array([[ 0.03792232, -0.03162944],
       [ 0.03731457, -0.03112254],
       [ 0.03814722, -0.03181702]]))
('self.dOut_dNet', array([[0.0657178 , 0.05696559]]))
('self.delta', array([[ 0.00249217, -0.00180179],
  

('self.dW', array([[ 0.00152063, -0.001106  ],
       [ 0.00147213, -0.00107073],
       [ 0.00153866, -0.00111911]]))
('calc_dETotal_dOut', array([[-0.00507499, -0.00219241],
       [-0.00328329, -0.00154405],
       [-0.00406508, -0.00235478]]))
('self.weights', array([[-2.0848995 ,  1.23835888],
       [-1.37092373,  0.88641614],
       [-1.66023358,  1.32225009]]))
H1
('get_dETotal_dOut', array([-0.0072674 , -0.00482734, -0.00641986]))
('dETotal_dOut', array([-0.0072674 , -0.00482734, -0.00641986]))
('self.dOut_dNet', array([[0.23446037, 0.2368633 , 0.23352648]]))
('self.delta', array([[-0.00170392, -0.00114342, -0.00149921]]))
('self.dW', (1, 3), (1, 2))
('self.dW', array([[-8.51959024e-05, -5.71709919e-05, -7.49603917e-05],
       [-1.70391805e-04, -1.14341984e-04, -1.49920783e-04]]))
('calc_dETotal_dOut', array([[-0.00120115, -0.00099929, -0.00142241],
       [-0.00211491, -0.00083535, -0.00191453]]))
('self.weights', array([[0.70497575, 0.8739807 , 0.94881129],
       [1.241288

KeyboardInterrupt: 